In [31]:
import pandas as pd
import plotly.express as px
import numpy as np
from pathlib import Path

result_dir = Path("../../bench/results")

rust_dir = result_dir.joinpath("rs")
go_dir = result_dir.joinpath("go")

In [67]:
dayta = pd.DataFrame()

for i in range(1,4):
    for (lang_dir, lang) in [(rust_dir, "Rust"),(go_dir, "Go")]:
        df = pd.read_csv(lang_dir.joinpath(f"day_{i}.csv"))
        df['Lang'] = lang
        df['Day'] = i
        dayta = dayta.append(df)

for day in range(1,4):
    df = pd.read_csv(rust_dir.joinpath(f"day_{day}_cargo.csv"))

    for part in ['read', 'part 1', 'part 2', 'total']:
        median_time = df[(df['Part'] == part) & (df['Run'] == 1)]['Elapsed (ns)'].values[0]
        min_time = df[(df['Part'] == part) & (df['Run'] == 2)]['Elapsed (ns)'].values[0]
        max_time = df[(df['Part'] == part) & (df['Run'] == 3)]['Elapsed (ns)'].values[0]
        num_buckets = int((max_time - min_time) / 100)
        max_count = 0

        for lang in ['Rust', 'Go']:
            res = dayta[(dayta['Lang'] == lang) & (dayta['Part'] == part) & (dayta['Day'] == day)]['Elapsed (ns)']
            if res.max() < 100:
                max_count = res.count()
                continue
            counts, bins = np.histogram(res, bins=range(0, int(res.max()), 100))
            if counts.max() > max_count:
                max_count = counts.max()

        half_max = int(max_count/2)
        times = np.repeat(median_time, max_count)
        
        if num_buckets > 0:
            times = np.concatenate(
                (
                    times,
                    np.repeat(min_time, half_max),
                    np.repeat(max_time, half_max),
                )
            )
        med = pd.DataFrame(times, columns=['Elapsed (ns)'])
        med['Part'] = part
        med['Day'] = day
        med['Lang'] = 'Rust (Cargo)'
        med['Run'] = 1
        med['Max. memory (B)'] = 0
        med[' Num. allocations'] = 0
        dayta = dayta.append(med)
        print(f'Day {day}, Part {part}: {num_buckets}')


Day 1, Part read: 5
Day 1, Part part 1: 0
Day 1, Part part 2: 1
Day 1, Part total: 8
Day 2, Part read: 2
Day 2, Part part 1: 0
Day 2, Part part 2: 0
Day 2, Part total: 0
Day 3, Part read: 18
Day 3, Part part 1: 2
Day 3, Part part 2: 20
Day 3, Part total: 126


In [54]:
dayta[dayta['Lang'] == 'Rust (Cargo)'].count()

Part                 55034
Run                  55034
Elapsed (ns)         55034
Max. memory (B)      55034
 Num. allocations    55034
Lang                 55034
Day                  55034
dtype: int64

In [68]:
from pandas.api.types import CategoricalDtype

dayta.loc[dayta['Part'] == 'read', 'Part'] = 'Parse Data'
dayta.loc[dayta['Part'] == 'part 1', 'Part'] = 'Part 1'
dayta.loc[dayta['Part'] == 'part 2', 'Part'] = 'Part 2'
dayta.loc[dayta['Part'] == 'total', 'Part'] = 'Total'
dayta['Day'] = 'Day ' + dayta['Day'].astype(str)
dayta['Lang'] = dayta['Lang'].astype(CategoricalDtype(categories=['Rust (Cargo)', 'Rust', 'Go'], ordered = True))
dayta['Part'] = dayta['Part'].astype(CategoricalDtype(categories=['Parse Data', 'Part 1', 'Part 2', 'Total'], ordered = True))
dayta.sort_values(by=['Lang', 'Day','Part'], inplace=True)

fig = px.histogram(
    dayta,
    nbins=10240,
    x= 'Elapsed (ns)',
    color='Lang',
    facet_col='Part',
    facet_row='Day',
    barmode='overlay',
    title = 'Advent of Code 2021',
    marginal="box",
    hover_name='Lang',
    color_discrete_map={
        'Rust (Cargo)': '#ffc9a9',
        'Rust': '#f04c00',
        'Go': '#7fd5ea',
    },
    hover_data=['Elapsed (ns)'],
    opacity=0.7,
    height=800,
    )
fig.update_layout(
    yaxis_title = 'Count',
    font={
        "family": "Arial, bold",
    },
)
fig.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
fig.update_xaxes(matches=None, showticklabels=True)
fig.update_yaxes(matches=None)

fig.show()